In [1]:
import ROOT
import numpy as np
from utils import *

%jsroot on

Welcome to JupyROOT 6.28/00


In [2]:
def get_cross_section(file_name: str, xbins: list[float]) -> ROOT.TH1D:
    """Take a file name as a string and returns the cross section """

    file = open(file_name, "r")
    file.readline()
    
    energy = []
    crossSection = []

    for line in file:
        values = line.strip().split(',')
        energy.append(float(values[0]))  # eV
        crossSection.append(float(values[1]))  # barns

    file.close()


    graph = ROOT.TGraph(len(energy), np.array(energy), np.array(crossSection))

    hEn_sig_tot_10Bo = ROOT.TH1D("hEn_sig_tot_10Bo", "hEn_sig_tot_10Bo; Energy [eV]; Cross Section [b]", len(xbins)-1, xbins)

    for i in range(1, len(xbins)):
        x = hEn_sig_tot_10Bo.GetBinCenter(i)
        y = graph.Eval(x)
        hEn_sig_tot_10Bo.SetBinContent(i, y)

    return hEn_sig_tot_10Bo

In [3]:
def get_beam_intensity(file_name: str, cross_section: ROOT.TH1D) -> ROOT.TH1D:
    """Test"""
    
    file_in = ROOT.TFile(file_name)
    # dir=file_in.Get("hEn_all_gate_Bo")
    # hEn_all_gate_Bo = dir.Get("hEn_all_gate_Bo")
    hEn_all_gate_Bo = file_in.Get("hEn_all_gate_Bo")
    hEn_all_gate_Bo.SetDirectory(0)

    beam_intensity = hEn_all_gate_Bo

    # print(cross_section.GetNbinsX())
    # print(beam_intensity.GetNbinsX())
    
    # beam_intensity.SetName("beam_intensity")
    # beam_intensity.GetYaxis().SetName("")
    beam_intensity.Divide(cross_section)

    return beam_intensity

In [4]:
Nbins = 100000
down = 0
up =100000

xbins_En = get_xbins_En_10ns(Nbins,down, up,21.5)

In [5]:
cross_section = get_cross_section("data/nndc_data.txt", xbins_En)
cross_section.Draw()
ROOT.gROOT.GetListOfCanvases().Draw()

Info in <TCanvas::MakeDefCanvas>:  created default TCanvas with name c1


In [6]:
beam_intensity = get_beam_intensity("stage0_output.root", cross_section)
beam_intensity.Draw()
beam_intensity.SetName("hEn_beam_intensity")
beam_intensity.SetTitle("hEn_beam_intensity")
beam_intensity.GetYaxis().SetTitle("Intensity [A.U.]")
ROOT.gROOT.GetListOfCanvases().Draw()

In [40]:
# def beam_corr (hist: ROOT.TH1, beam_intensity_hist: ROOT.TH1) -> ROOT.TH1:

#     corr_string = "_beamcorr"
    
#     hist.Divide(beam_intensity_hist)
#     hist.SetName(hist.GetName() + corr_string)
    
    
#     return hist





def apply_beam_corr (hist_dict: dict, beam_intensity_hist: ROOT.TH1):
    """Takes a file name and a beam intensity histogram and applies it to all hEn histograms"""
    
    def beam_corr(hist_dict: dict, new_hist_dict: dict):
        """Takes a dictionary and recursively writes to a TDirectoryFile"""

        for key, hist in hist_dict.items():

            if type(hist) is dict:
    
                if "hEn" in key:
                    key = key + "_beamcorr"
                new_hist_dict[key] = {}
                beam_corr(hist,new_hist_dict[key])
                
            else:
                
                if "hEn" in key:
                    # print(f"correcting {hist.GetName()}")
                    hist.Multiply(beam_intensity_hist)
                    hist.SetName(hist.GetName() + "_beamcorr")
                    key = key + "_beamcorr"

                new_hist_dict[key] = hist
                

    new_hist_dicts = {}
    beam_corr(hist_dict, new_hist_dicts)

    return new_hist_dicts


In [41]:
hist_dict = read_root_to_dict("stage0_output.root")

In [42]:
new_hist_dict = apply_beam_corr(hist_dict, beam_intensity)

AttributeError: 'TH1D' object has no attribute 'multiply'

In [ ]:
write_dict_to_root(new_hist_dict, "stage1_output.root")